## Collecting older reddit posts using PushShift and API wrappers

In [3]:
import psaw
from psaw import PushshiftAPI
import datetime as dt
import pandas as pd
import praw

## for comment scraping, enter your user-agent and user-secret here

In [4]:
import pandas as pd
import numpy as np

import datetime as dt
import time
import requests
import json

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.expand_frame_repr', False)
np.random.seed(42)

import string
import re 
from bs4 import BeautifulSoup
import nltk
from nltk.corpus import stopwords

from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn import metrics
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer

### Submissions

We create an api variable and set the start time for our data collection (in this case 12/10/2018).

In [5]:
api = PushshiftAPI()

In [6]:
headers = {'User-agent': 'Amy_bot'}

In [7]:
start_time = int(dt.datetime(2006, 1, 1).timestamp())

Now we search for submissions using search terms well documented on the PushShift/Reddit sites:

In [8]:
men_sub = list(api.search_submissions(
                   after=start_time,
                   subreddit='men',
                   filter=['author', 'title', 'url','id','subreddit','created'],
                   limit=100000))

In [9]:
women_sub = list(api.search_submissions(
                   after=start_time,
                   subreddit='women',
                   filter=['author', 'title', 'url','id','subreddit','created'],
                   limit=100000))

In [10]:
len(men_sub)

4299

In [11]:
len(women_sub)

51717

In [12]:
men_sub

[submission(author='Arvindfashioning', created_utc=1546354863, id='abirf0', subreddit='men', title='Affordable Jeans for Men Online | NNNOW.com', url='https://www.nnnow.com/men_jeans', created=1546372863.0, d_={'author': 'Arvindfashioning', 'created_utc': 1546354863, 'id': 'abirf0', 'subreddit': 'men', 'title': 'Affordable Jeans for Men Online | NNNOW.com', 'url': 'https://www.nnnow.com/men_jeans', 'created': 1546372863.0}),
 submission(author='Lurd-TK', created_utc=1546351057, id='abicso', subreddit='men', title='3 Crucial Things You Should Know About Women', url='http://www.toplovehacks.com.ng/2019/01/01/things-you-should-know-about-women.html', created=1546369057.0, d_={'author': 'Lurd-TK', 'created_utc': 1546351057, 'id': 'abicso', 'subreddit': 'men', 'title': '3 Crucial Things You Should Know About Women', 'url': 'http://www.toplovehacks.com.ng/2019/01/01/things-you-should-know-about-women.html', 'created': 1546369057.0}),
 submission(author='0hLuckyMan', created_utc=1546290457, i

In [13]:
women_sub

[submission(author='vWords7', created_utc=1546394467, id='abona9', subreddit='women', title='Happy New Year Animation with Music', url='https://www.reddit.com/r/women/comments/abona9/happy_new_year_animation_with_music/', created=1546412467.0, d_={'author': 'vWords7', 'created_utc': 1546394467, 'id': 'abona9', 'subreddit': 'women', 'title': 'Happy New Year Animation with Music', 'url': 'https://www.reddit.com/r/women/comments/abona9/happy_new_year_animation_with_music/', 'created': 1546412467.0}),
 submission(author='sadatay', created_utc=1546377376, id='abm38l', subreddit='women', title='Single Moms Get Sucked Into the Cruelest Debtors’ Prison We’ve Ever Seen', url='https://www.aclu.org/blog/racial-justice/race-and-criminal-justice/single-moms-get-sucked-cruelest-debtors-prison-weve', created=1546395376.0, d_={'author': 'sadatay', 'created_utc': 1546377376, 'id': 'abm38l', 'subreddit': 'women', 'title': 'Single Moms Get Sucked Into the Cruelest Debtors’ Prison We’ve Ever Seen', 'url':

In [14]:
type(men_sub[0])

psaw.PushshiftAPI.submission

In [15]:
type(women_sub[0])

psaw.PushshiftAPI.submission

In [16]:
title = []
id_df = []
url = []
subreddit = []
created = []

In [17]:
title = []
id_df = []
url = []
subreddit = []
created = []

for i in range(1, len(men_sub)):
    title.append(men_sub[i].title)
    id_df.append(men_sub[i].id)
    url.append(men_sub[i].url)
    subreddit.append(men_sub[i].subreddit)
    created.append(men_sub[i].created)

In [18]:
for i in range(1, len(women_sub)):
    title.append(women_sub[i].title)
    id_df.append(women_sub[i].id)
    url.append(women_sub[i].url)
    subreddit.append(women_sub[i].subreddit)
    created.append(women_sub[i].created)

In [19]:
df = pd.DataFrame({'title':title, 'id':id_df,'subreddit':subreddit,'url':url,'created':created})

In [20]:
df.tail()

title     id subreddit                                                url       created
56009  The "Generic" Woman's Vote Proves To Be Anythi...  67x0t     women  http://www.alternet.org/reproductivejustice/76...  1.202365e+09
56010               Feminist Ultimatums: Not In Our Name  67whk     women  http://www.alternet.org/reproductivejustice/76...  1.202355e+09
56011  Conservapedia blames murdered marine for own m...  67k5s     women  http://totaldrek.blogspot.com/2008/01/this-mak...  1.202110e+09
56012  Conservapedia blames murdered marine for own m...  67k5r     women  http://totaldrek.blogspot.com/2008/01/this-mak...  1.202110e+09
56013       Women in Open Source conference, Feb 8, 2008  67bb6     women  http://www.socallinuxexpo.org/scale6x/conferen...  1.201859e+09

In [21]:
df.shape

(56014, 5)

In [23]:
df.info

<bound method DataFrame.info of                                                    title      id subreddit                                                url       created
0           3 Crucial Things You Should Know About Women  abicso       men  http://www.toplovehacks.com.ng/2019/01/01/thin...  1.546369e+09
1      Going to celebrate 20 years of marriage by din...  abb9rs       men  https://www.reddit.com/r/men/comments/abb9rs/g...  1.546308e+09
2                           The Men 'Me Too' Left Behind  aao4n5       men  https://www.huffingtonpost.com/entry/me-too-tr...  1.546130e+09
3      I Was a Bully in School. Now, My Son Was Becom...  aan2xj       men  https://www.yahoo.com/lifestyle/bully-school-n...  1.546123e+09
4                How do you prepare yourself for a date?  aajqqe       men  https://www.reddit.com/r/men/comments/aajqqe/h...  1.546092e+09
5       Man Period, Man-struation, Testosterone Cycle...  aadehu       men  https://www.reddit.com/r/men/comments/aadehu/m...  1

In [24]:
#Save file to be analyzed in another notebook
df.to_csv('./reddit_gender_all.csv')

In [31]:
#women's first url
url[56013] #feb 8 2008

'http://www.socallinuxexpo.org/scale6x/conference-info/women-in-open-source/'

In [32]:
#men's first url
url[4296] #Aug 1 2008

'http://boysite.info/blog/?p=89'

In [28]:
print (url[len(men_sub)])

https://www.reddit.com/r/women/comments/abm2lt/i_nicked_myself_near_my_bits_nsfw/


In [33]:
print (url[len(women_sub)])

http://www.thestar.com/news/canada/article/774649--conservatives-eye-new-lyrics-for-our-national-anthem?bn=1
